# Intro til Keglesnit

Demo af Christian Mikkelstrup og Hans Henrik Hermansen

In [ ]:
from sympy import *
init_printing()
from dtumathtools import *

## Identifikation af et keglesnit

Vi betragter en mængde $M$ af punkter i planen, der beskrives af ligningen

$$
11x^2 - 24 x y + 4 y^2 - 20 x + 40  y - 60 = 0
$$

Dette er en andengradsligning i to varaible. Den fremstiller et keglesnit, og vi er interesseret i, hvilket keglesnit det er. Det burde jo være lige til, da vi har en masse ligninger, der beskriver formen af de forskellige keglesnit, så vi burde bare kunne tjekke, hvilken der passer til vores ligning. Det er der bare ingen af dem, der gør, da vores ligning indeholder blandede led. Derfor er vi nødt til at lave et basisskifte.

Vi opskriver ligningen på matrixform

In [ ]:
x,y = symbols("x y")
var_vec = Matrix([x,y])
lignM = Eq(11*x**2 - 24*x*y + 4*y**2 - 20*x + 40*y - 60,0)
H = dtutools.hessian(lignM.lhs)
A = S(1)/2 * H
k = (var_vec.T * S(1)/2 * H * var_vec)[0].expand()
l = (Matrix([-20,40]).T * var_vec)[0].expand()

A,k,l, k + l - 60

Det hele ser ud som forventet. Nu vil vi fjerne de blandede led. Dette gør vi ved at diagonalisere $A$. Først finder vi egenvektorerne:

In [ ]:
A.eigenvects()

Da $A$ er symmetrisk vil de to tilhørende egenvektor være ortogonale på hinanden.
Vi finder en enhedsvektor i både $E_{20}$ og $E_{-5}$

In [ ]:
q1 = Matrix([S(3)/4,1])
q2 = Matrix([-S(4)/3,1])
q1 = q1.normalized()       # Eller q1 = q1 / sqrt((q1.T * q1)[0])
q2 = q2.normalized()       # q2 = q2 / sqrt((q2.T * q2)[0])

q1, q2

Vi ved nu at matricen $[ q1 \mid q2 ]$ er ortogonal. Det eneste vi skal sikre os er, at den er positiv ortogonal.

In [ ]:
Q = Matrix.hstack(q1,q2)
Q.det()

Det var den. Hvis ikke den var, kunne vi bare have byttet om på søjlerne, så vi havde fået $Q = [ q2 \mid q1 ]$.

Vi har et nyt koordinat system $(O,q1,q2)$, som svarer til en drejning af det givne koordinat system. Sammenhængen mellem de gamle koordinater $(x,y)=({}_e x,{}_e y)$ og de nye $({}_q x ,{}_q y)$ er
$$
\begin{bmatrix} {}_e x \\ {}_e y \end{bmatrix} = Q \begin{bmatrix} {}_q x \\ {}_q y \end{bmatrix}.
$$
da $Q = {}_e M_q$.

Vi sætter $\Lambda = \begin{bmatrix} -5 & 0 \\ 0 & 20 \end{bmatrix}$, og der skal så nu gælde
$$
Q ^ T A Q = \Lambda.
$$

In [ ]:
Lambda = Matrix([[-5,0],[0,20]])
Eq(Lambda,Q.T * A * Q)

Nu kan vi opstille vores ligning i det drejede koordinatsystem, hvor vi for nemhedsskyld omdøber $({}_q x ,{}_q y)$ til $(x_1 ,y_1)$.

In [ ]:
x1,y1 = symbols("x1 y1")
var_vec_1 = Matrix([x1,y1])
lignM_1 = (var_vec_1.T * Q.T * A * Q * var_vec_1)[0] + (Matrix([-20,40]).T * Q * var_vec_1)[0] - 60
Eq(lignM_1,0)


Her bruger vi **kvadratkomplettering** til at omskrive ligningen til det følgende

In [ ]:
-5*(x1-2)**2,expand(-5*(x1-2)**2), 20*(y1+1)**2,expand(20*(y1+1)**2)

Vi kan her se, at de to konstanter, der opstår går ud med hinanden, så vi kan bare skrive de nye led direkte in i ligningen.

In [ ]:
lign = Eq((-5 * (x1 - 2) ** 2 + 20 * (y1 + 1) ** 2 - 60),0)
lign

In [ ]:
lign = Eq((lign.lhs + 60) / 60, (lign.rhs + 60) / 60)
lign

Dette er en hyperbel med halvakserne $\sqrt{3}$ og $\sqrt{12}$. Vi kan finde centrum i det givne koordinatsystem vha. basisskifte. Koordinaterne $(x_1,y_1)$ er = $(2,-1)$
Vi finder dem for $(x,y)$

In [ ]:
Q * Matrix([2,-1])

Nu er 1. aksen er linjen gennem hyperblens centrum med $e1$ som retningsvektor, og 2. aksen er linjen, der går gennem hyperblens centrum med $e2$ som retningsvektor.
Asymptoterne er givet ved $y_1 + 1= \pm \frac{\sqrt{3}}{\sqrt{12}}(x_1 - 2) = \pm \frac{1}{2}(x_1-2)$

Nu oversætter vi asymptoterne til det koordinatsystem.

In [ ]:
((Q * Matrix([S(1)/2,1])).T * var_vec)[0], ((Q * Matrix([-S(1)/2,1])).T * var_vec)[0] + 2

In [ ]:
t = symbols("t")
M = dtuplot.plot_implicit(lignM,(x,-4,8),(y,-6,6),show=False,aspect="equal",size=(6,6))
sym1 = dtuplot.plot_parametric(2 + e1[0]*t,1 + e1[1]*t,(t,-20,20),show=False)
sym2 = dtuplot.plot_parametric(2 + e2[0]*t,1 + e2[1]*t,(t,-20,20),show=False)
asymp1 = dtuplot.plot_implicit(Eq(-x/S(2)+y,0),(x,-4,8),(y,-6,6),show=False)
asymp2 = dtuplot.plot_implicit(Eq(-S(11)*x/10+y/S(5)+2,0),(x,-4,8),(y,-6,6),show=False)
e1p = dtuplot.quiver(Matrix([2,1]),e1 * 2, rendering_kw={"color":"black"},show=False)
e2p = dtuplot.quiver(Matrix([2,1]),e2 * 2, rendering_kw={"color":"black"},show=False)

M.extend(sym1)
M.extend(sym2)
M.extend(asymp1)
M.extend(asymp2)
M.extend(e1p)
M.extend(e2p)

#fjern legend
M.legend = False

M.show()
